In [21]:
import numpy as np
import xarray as xr
from matplotlib import pyplot as plt
import matplotlib as mpl
import pandas as pd
import cartopy.crs  as ccrs
import os
import datetime
from datetime import timedelta
from datetime import datetime
from matplotlib import ticker
from matplotlib.axes import Axes
from cartopy.mpl.geoaxes import GeoAxes
import cartopy.feature as cfeature
import geopandas as gp
import matplotlib.patheffects as pe
from matplotlib.lines import Line2D
from scipy import stats
from scipy.stats import linregress
import matplotlib.patches as patches

import WetBulb

GeoAxes._pcolormesh_patched = Axes.pcolormesh

In [6]:
def remove_time_mean(x):
    return x - x.mean(dim='time')

def standardize(x):
    return x/x.std(dim = 'time')

def CtoF(x):
    return x*9/5 + 32

In [7]:
stn_folder = '/dx01/ivanov/data/HadISD_stationdata/brazil_heatwave/raw_station_data/'

# Rio stations
galeao_name = 'hadisd.3.4.0.2023f_19310101-20240101_837460-99999.nc'
campo_name = 'hadisd.3.4.0.2023f_19310101-20240101_837480-99999.nc'
santos_name = 'hadisd.3.4.0.2023f_19310101-20240101_837550-99999.nc'

galeao = xr.open_dataset(stn_folder + galeao_name)
campo = xr.open_dataset(stn_folder + campo_name)
santos = xr.open_dataset(stn_folder + santos_name)

In [8]:
galeao_winddir = galeao.winddirs
galeao_windspeed = galeao.windspeeds

In [9]:
# Change flagged values to nan
galeao_temp = galeao.temperatures.where(galeao.temperatures > -2*np.exp(30))
campo_temp = campo.temperatures.where(campo.temperatures > -2*np.exp(30))
santos_temp = santos.temperatures.where(santos.temperatures > -2*np.exp(30))

# Calculate daily max
galeao_Tmax = galeao_temp.resample(time="1D").max(dim='time')
campo_Tmax = campo_temp.resample(time="1D").max(dim='time')
santos_Tmax = santos_temp.resample(time="1D").max(dim='time')

In [10]:
galeao_winddir_mean = galeao_winddir.resample(time="1D").mean(dim='time')
galeao_windspeed_mean = galeao_windspeed.resample(time="1D").mean(dim='time')

In [11]:
station = galeao
stn_temp = galeao_temp

In [12]:
# Refine study period to later time with reliable data
stn_Tmax = galeao_Tmax.sel(time = slice('01-01-1972','01-15-2024'))
stn_winddir = galeao_winddir_mean.sel(time = slice('01-01-1972','01-15-2024'))
stn_windspeed = galeao_windspeed_mean.sel(time = slice('01-01-1972','01-15-2024'))

# Figure 1

In [14]:
stn_2023 = stn_Tmax.sel(time = slice('01-01-2023','12-31-2023'))

# Calculate annual climatology, plot 2023 on top of that
stn_clim = stn_Tmax.groupby('time.dayofyear').mean('time')
stn_std = stn_Tmax.groupby('time.dayofyear').std('time')
stn_95 = stn_Tmax.groupby('time.dayofyear').quantile(0.99, dim = 'time')
stn_2023_plot = stn_2023.groupby('time.dayofyear').mean('time')

In [15]:
# Smooth climatology
stn_clim_smoothed = stn_clim.rolling(dayofyear=10, center=True).mean()
stn_std_smoothed = stn_std.rolling(dayofyear=10, center=True).mean()

In [16]:
# Plot the same thing for specific humidity
stn_dewpoints = station.dewpoints.where(station.dewpoints > -2*np.exp(30))

sp_mb = station.stnlp.where(station.stnlp > -2*np.exp(30))

# Specific humidity (in kg/kg)
vap_pres = 6.112*np.exp((17.67*stn_dewpoints)/(stn_dewpoints + 243.5))

In [17]:
# Calculate q using station data for station level pressure

# Calculate q using pressure approximation based on elevation 
h = station.elevation.values
p = 101325*(1 - 2.25577*(10**(-5))*h)**5.25588/100

q = (0.622 * vap_pres)/(p - (0.378 * vap_pres))

stn_qmean = q.resample(time="1D").mean(dim='time')
stn_qmean = stn_qmean.sel(time = slice('01-01-1972','12-31-2023'))

In [18]:
stn_2023q = stn_qmean.sel(time = slice('01-01-2023','12-31-2023'))

# Calculate annual climatology, plot 2023 on top of that
stn_climq = stn_qmean.groupby('time.dayofyear').mean('time')
stn_stdq = stn_qmean.groupby('time.dayofyear').std('time')
stn_95q = stn_qmean.groupby('time.dayofyear').quantile(0.99, dim = 'time')
stn_2023_plotq = stn_2023q.groupby('time.dayofyear').mean('time')

In [19]:
# Smooth climatology
stn_climq_smoothed = stn_climq.rolling(dayofyear=10, center=True).mean()
stn_stdq_smoothed = stn_stdq.rolling(dayofyear=10, center=True).mean()

In [22]:
# Calculate using surface pressure approximation
Twb,Teq,epott = WetBulb.WetBulb(stn_temp, p*100*np.ones(np.shape(stn_temp)), q, HumidityMode = 0)

print('Wet bulb has been calculated')

stn_Twmax = Twb.resample(time="1D").max(dim='time')
stn_Twmax = stn_Twmax.sel(time = slice('01-01-1972','12-31-2023'))

Wet bulb has been calculated


In [23]:
stn_2023Tw = stn_Twmax.sel(time = slice('01-01-2023','12-31-2023'))

# Calculate annual climatology, plot 2023 on top of that
stn_climTw = stn_Twmax.groupby('time.dayofyear').mean('time')
stn_stdTw = stn_Twmax.groupby('time.dayofyear').std('time')
stn_95Tw = stn_Twmax.groupby('time.dayofyear').quantile(0.99, dim = 'time')
stn_2023_plotTw = stn_2023Tw.groupby('time.dayofyear').mean('time')

In [24]:
# Smooth climatology
stn_climTw_smoothed = stn_climTw.rolling(dayofyear=10, center=True).mean()
stn_stdTw_smoothed = stn_stdTw.rolling(dayofyear=10, center=True).mean()

In [25]:
np.max(stn_2023_plotTw)

<xarray.DataArray ()>
array(28.19036047)

In [28]:
# Stacked plot with all three
fig, axs = plt.subplots(3,1, figsize = (10,14), dpi = 1200)
xticks = ['Jan','Feb','Mar','Apr','May','Jun','Jul','Aug','Sep','Oct','Nov','Dec']

axs[0].plot(stn_clim_smoothed.dayofyear, stn_clim_smoothed, c = 'k', linewidth = 5)
axs[0].fill_between(stn_clim.dayofyear,stn_clim-stn_std_smoothed, stn_clim+stn_std_smoothed, color = 'k', alpha = 0.2)
axs[0].fill_between(stn_clim.dayofyear,stn_clim-2*stn_std_smoothed, stn_clim+2*stn_std_smoothed, color = 'k', alpha = 0.2)
axs[0].plot(stn_2023_plot.dayofyear, stn_2023_plot, c = 'crimson')
axs[0].set_ylabel('Temperature (C)')
axs[0].set_ylim([15,43]) # For Rio

axs[0].set_xticks([0,32,61,92,122,153,183,214,245,275,306,336])
axs[0].set_xticklabels(xticks)

line1 = Line2D([0], [0], color='k', alpha = 1, linestyle = 'solid', linewidth = 4)
line2 = Line2D([0], [0], color='dimgrey', alpha = 0.2, linestyle = 'solid', linewidth = 4)
line3 = Line2D([0], [0], color='dimgrey', alpha = 0.4, linestyle = 'solid', linewidth = 4)
line4 = Line2D([0], [0], color='r', alpha = 1, linestyle = 'solid', linewidth = 2)
labels = ['Climatology', '1 Std', '2 Std', '2023 T']

axs[0].legend([line1, line2,line3, line4],labels, loc = 'lower left', framealpha=1, fontsize = 10).set_zorder(100)

axs[1].plot(stn_climq_smoothed.dayofyear, 1000*stn_climq_smoothed, c = 'k', linewidth = 5)
axs[1].fill_between(stn_climq.dayofyear,1000*(stn_climq-stn_stdq_smoothed), 1000*(stn_climq+stn_stdq_smoothed), color = 'k', alpha = 0.2)
axs[1].fill_between(stn_climq.dayofyear,1000*(stn_climq-2*stn_stdq_smoothed), 1000*(stn_climq+2*stn_stdq_smoothed), color = 'k', alpha = 0.2)
axs[1].plot(stn_2023_plotq.dayofyear, 1000*stn_2023_plotq, c = 'teal')
axs[1].set_ylabel('Specific Humidity (g/kg)')
axs[1].set_xticks([0,32,61,92,122,153,183,214,245,275,306,336])
axs[1].set_xticklabels(xticks)

line5 = Line2D([0], [0], color='teal', alpha = 1, linestyle = 'solid', linewidth = 2)
axs[1].legend([line5],['2023 Specific Humidity'], loc = 'lower left', framealpha=1, fontsize = 10).set_zorder(100)

axs[2].plot(stn_climTw_smoothed.dayofyear, stn_climTw_smoothed, c = 'k', linewidth = 5)
axs[2].fill_between(stn_climTw.dayofyear,(stn_climTw-stn_stdTw_smoothed), (stn_climTw+stn_stdTw_smoothed), color = 'k', alpha = 0.2)
axs[2].fill_between(stn_climTw.dayofyear,(stn_climTw-2*stn_stdTw_smoothed), (stn_climTw+2*stn_stdTw_smoothed), color = 'k', alpha = 0.2)
axs[2].plot(stn_2023_plotTw.dayofyear, stn_2023_plotTw, c = 'purple')

axs[2].set_xlabel('Date')
axs[2].set_xticks([0,32,61,92,122,153,183,214,245,275,306,336])
axs[2].set_xticklabels(xticks)
axs[2].set_ylabel('Wet Bulb (C)')

line6 = Line2D([0], [0], color='purple', alpha = 1, linestyle = 'solid', linewidth = 2)
axs[2].legend([line6],['2023 Wet Bulb'], loc = 'lower left', framealpha=1, fontsize = 10).set_zorder(100)

axs[0].axvline(x = 322, color = 'dimgrey', linestyle = 'dashed', linewidth = 1.5, zorder = 0)
axs[1].axvline(x = 322, color = 'dimgrey', linestyle = 'dashed', linewidth = 1.5, zorder = 0)
axs[2].axvline(x = 322, color = 'dimgrey', linestyle = 'dashed', linewidth = 1.5, zorder = 0)

# Plot white blocks over beginning and end
rect1 = patches.Rectangle((0, 15), 10, 25, facecolor='w', zorder =10)
rect2 = patches.Rectangle((366-10, 15), 10, 25, facecolor='w', zorder =10)
axs[0].add_patch(rect1)
axs[0].add_patch(rect2)

rect3 = patches.Rectangle((0, 8), 10, 21-8, facecolor='w', zorder =10)
rect4 = patches.Rectangle((366-10, 8), 10, 21-8, facecolor='w', zorder =10)
axs[1].add_patch(rect3)
axs[1].add_patch(rect4)

rect5 = patches.Rectangle((0, 15), 10, 29-15, facecolor='w', zorder =10)
rect6 = patches.Rectangle((366-10, 15), 10, 29-15, facecolor='w', zorder =10)
axs[2].add_patch(rect5)
axs[2].add_patch(rect6)

# Add A, B, C markers
import string

axs[0].text(-35, 43.5, string.ascii_lowercase[0], size=20, weight='bold')
axs[1].text(-35, 21.5, string.ascii_lowercase[1], size=20, weight='bold')
axs[2].text(-35, 30, string.ascii_lowercase[2], size=20, weight='bold')

plt.savefig('Figure1.png')

plt.show()